In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [2]:
import os
folder_path = '/content/drive/MyDrive/Projects/ULX3s-Superresolution-CNN'
os.chdir(folder_path)

In [ ]:
!git init
!git status

Reinitialized existing Git repository in /content/drive/MyDrive/Projects/ULX3s-Superresolution-CNN/.git/
Refresh index: 100% (36/36), done.
On branch main
Your branch is up to date with 'origin/main'.

Changes not staged for commit:
  (use "git add <file>..." to update what will be committed)
  (use "git restore <file>..." to discard changes in working directory)
  (commit or discard the untracked or modified content in submodules)
	modified:   Efficient-Teacher-Student-Distillative-Super-Resolution-Model (new commits, untracked content)

Untracked files:
  (use "git add <file>..." to include in what will be committed)
	Pytorch_model_weights.ipynb
	formatted_weights.txt

no changes added to commit (use "git add" and/or "git commit -a")


In [ ]:
!git config --global user.email "advikbahadur@gmail.com"
!git config --global user.name "ADVIKBAHADUR"

In [ ]:
!git add .
!git commit -m "Added Pytorch to weights File"

[main 49db6fc] Added Pytorch to weights File
 1 file changed, 1 insertion(+), 1 deletion(-)
 rewrite Pytorch_model_weights.ipynb (75%)


In [ ]:
!git push

fatal: could not read Username for 'https://github.com': No such device or address


In [3]:
def format_fixed_point_value(value, num_bits):
    if value < 0:
        return f"-{num_bits}'sd{-value}"
    else:
        return f"{num_bits}'sd{value}"

def extract_and_format_weights(model):
    frac_bits = 16  # Number of fractional bits for fixed-point representation
    scale_factor = 2 ** frac_bits  # Scaling factor based on the fractional bits

    # Collect all convolution weights
    conv_weights = []
    conv_layer_indices = []

    for name, param in model.named_parameters():
        if 'conv' in name and 'weight' in name:
            weights = param.data.cpu().numpy()
            weights_scaled = np.round(weights * scale_factor).astype(np.int32)
            conv_weights.append(weights_scaled)
            conv_layer_indices.append(name.replace('.', '_'))

    # Determine the size of the 5D register
    total_convs = len(conv_weights)
    max_kernels = max(w.shape[0] for w in conv_weights)
    max_depth = max(w.shape[1] for w in conv_weights)
    max_height = max(w.shape[2] for w in conv_weights)
    max_width = max(w.shape[3] for w in conv_weights)

    formatted_weights = f"// 5D Register to store convolution weights: [ConvLayer][Kernel][Depth][Height][Width]\n"
    formatted_weights += f"// Fixed-point format: {frac_bits} fractional bits\n"
    formatted_weights += f"reg signed [31:0] conv_weights[0:{total_convs-1}][0:{max_kernels-1}][0:{max_depth-1}][0:{max_height-1}][0:{max_width-1}] = '{{\n"

    for conv_index, (weights_scaled, conv_name) in enumerate(zip(conv_weights, conv_layer_indices)):
        num_kernels, kernel_depth, kernel_height, kernel_width = weights_scaled.shape
        formatted_weights += f"// Weights for {conv_name}\n"
        formatted_weights += f"{{\n"
        for k in range(num_kernels):
            formatted_weights += f"{{\n"
            for d in range(kernel_depth):
                formatted_weights += "{"
                for i in range(kernel_height):
                    formatted_weights += "{"
                    for j in range(kernel_width):
                        int_value = weights_scaled[k, d, i, j]
                        num_bits = int_value.bit_length() + 1  # +1 for the sign bit
                        formatted_weights += format_fixed_point_value(int_value, num_bits)
                        if j < kernel_width - 1:
                            formatted_weights += ", "
                    formatted_weights += "}"
                    if i < kernel_height - 1:
                        formatted_weights += ", "
                formatted_weights += "}"
                if d < kernel_depth - 1:
                    formatted_weights += ",\n"
            formatted_weights += "}"
            if k < num_kernels - 1:
                formatted_weights += ",\n"
        formatted_weights += "}"
        if conv_index < total_convs - 1:
            formatted_weights += ",\n"
    formatted_weights += "};\n"

    return formatted_weights

In [4]:
import torch
import numpy as np

class StudentModel(torch.nn.Module):
    def __init__(self, scale_factor=4):
        super(StudentModel, self).__init__()
        self.upsample = torch.nn.Sequential(
            torch.nn.Conv2d(3, 3 * (scale_factor ** 2), kernel_size=3, stride=1, padding=1),
            torch.nn.PixelShuffle(scale_factor)
        )
        self.conv1 = torch.nn.Conv2d(3, 64, kernel_size=3, stride=1, padding=1)
        self.conv2 = torch.nn.Conv2d(64, 64, kernel_size=3, stride=1, padding=1)
        self.conv3 = torch.nn.Conv2d(64, 64, kernel_size=3, stride=1, padding=1)
        self.conv4 = torch.nn.Conv2d(64, 64, kernel_size=3, stride=1, padding=1)
        self.conv5 = torch.nn.Conv2d(64, 3, kernel_size=3, stride=1, padding=1)
        self.relu = torch.nn.ReLU(inplace=True)

    def forward(self, x):
        x = self.upsample(x)
        x = self.conv1(x)
        x = self.conv2(x)
        x = self.conv3(x)
        x = self.conv4(x)
        x = self.conv5(x)
        x = self.relu(x)
        return x

# Load your model with weights
model = StudentModel()  # Make sure to define your actual model class
model.load_state_dict(torch.load('/content/drive/MyDrive/Projects/ULX3s-Superresolution-CNN/Efficient-Teacher-Student-Distillative-Super-Resolution-Model/ESRGAN/models/SupervisedLossOnFeatureMaps_v2.pth'))  # Load the trained model weights

def extract_and_format_weights(model):
    frac_bits = 16  # Number of fractional bits for fixed-point representation
    scale_factor = 2 ** frac_bits  # Scaling factor based on the fractional bits

    # Collect all convolution weights
    conv_weights = []
    conv_layer_indices = []

    for name, param in model.named_parameters():
        if 'conv' in name and 'weight' in name:
            weights = param.data.cpu().numpy()
            weights_scaled = np.round(weights * scale_factor).astype(np.int32)
            conv_weights.append(weights_scaled)
            conv_layer_indices.append(name.replace('.', '_'))

    # Determine the size of the 5D register
    total_convs = len(conv_weights)
    max_kernels = max(w.shape[0] for w in conv_weights)
    max_depth = max(w.shape[1] for w in conv_weights)
    max_height = max(w.shape[2] for w in conv_weights)
    max_width = max(w.shape[3] for w in conv_weights)

    formatted_weights = f"// 5D Register to store convolution weights: [ConvLayer][Kernel][Depth][Height][Width]\n"
    formatted_weights += f"// Fixed-point format: {frac_bits} fractional bits\n"
    formatted_weights += f"reg signed [31:0] conv_weights[0:{total_convs-1}][0:{max_kernels-1}][0:{max_depth-1}][0:{max_height-1}][0:{max_width-1}] = '{{\n"

    for conv_index, (weights_scaled, conv_name) in enumerate(zip(conv_weights, conv_layer_indices)):
        num_kernels, kernel_depth, kernel_height, kernel_width = weights_scaled.shape
        formatted_weights += f"// Weights for {conv_name}\n"
        formatted_weights += f"{{\n"
        for k in range(num_kernels):
            formatted_weights += f"{{\n"
            for d in range(kernel_depth):
                formatted_weights += "{"
                for i in range(kernel_height):
                    formatted_weights += "{"
                    for j in range(kernel_width):
                        int_value = weights_scaled[k, d, i, j]
                        num_bits = int(int_value).bit_length() + 1  # +1 for the sign bit
                        formatted_weights += f"{num_bits}'sd{int_value}"
                        if j < kernel_width - 1:
                            formatted_weights += ", "
                    formatted_weights += "}"
                    if i < kernel_height - 1:
                        formatted_weights += ", "
                formatted_weights += "}"
                if d < kernel_depth - 1:
                    formatted_weights += ",\n"
            formatted_weights += "}"
            if k < num_kernels - 1:
                formatted_weights += ",\n"
        formatted_weights += "}"
        if conv_index < total_convs - 1:
            formatted_weights += ",\n"
    formatted_weights += "};\n"

    return formatted_weights

# Get formatted weights as Verilog arrays with optimized bit lengths
formatted_weights = extract_and_format_weights(model)

# Print or save the weights
print(formatted_weights)  # Or save them to a file if preferred


// 5D Register to store convolution weights: [ConvLayer][Kernel][Depth][Height][Width]
// Fixed-point format: 16 fractional bits
reg signed [31:0] conv_weights[0:4][0:63][0:63][0:2][0:2] = '{
// Weights for conv1_weight
{
{
{{15'sd8400, 15'sd-12340, 13'sd3527}, {15'sd-12066, 15'sd-11606, 13'sd-2983}, {14'sd5793, 14'sd4791, 14'sd6601}},
{{14'sd-4491, 12'sd1269, 13'sd3175}, {14'sd4569, 15'sd-9277, 12'sd-1853}, {14'sd7041, 15'sd10070, 15'sd-10451}},
{{15'sd9065, 14'sd4972, 15'sd8974}, {13'sd-2049, 13'sd2351, 15'sd-9675}, {13'sd-2470, 15'sd13758, 13'sd3394}}},
{
{{14'sd6521, 14'sd6441, 12'sd1938}, {13'sd3792, 14'sd7267, 15'sd8900}, {12'sd1063, 13'sd-2078, 13'sd-3476}},
{{14'sd-6434, 14'sd-5689, 12'sd1211}, {15'sd11563, 15'sd12513, 14'sd-4893}, {15'sd13114, 15'sd10153, 13'sd-4040}},
{{15'sd-9517, 15'sd8371, 14'sd-4571}, {15'sd12415, 15'sd8479, 14'sd7376}, {14'sd5703, 15'sd-9070, 15'sd-11924}}},
{
{{15'sd11783, 15'sd-8289, 15'sd8968}, {14'sd5811, 15'sd-12238, 11'sd-922}, {14'sd7923, 14'sd-56

In [8]:
import torch
import numpy as np

class StudentModel(torch.nn.Module):
    def __init__(self, scale_factor=4):
        super(StudentModel, self).__init__()
        self.upsample = torch.nn.Sequential(
            torch.nn.Conv2d(3, 3 * (scale_factor ** 2), kernel_size=3, stride=1, padding=1),
            torch.nn.PixelShuffle(scale_factor)
        )
        self.conv1 = torch.nn.Conv2d(3, 64, kernel_size=3, stride=1, padding=1)
        self.conv2 = torch.nn.Conv2d(64, 64, kernel_size=3, stride=1, padding=1)
        self.conv3 = torch.nn.Conv2d(64, 64, kernel_size=3, stride=1, padding=1)
        self.conv4 = torch.nn.Conv2d(64, 64, kernel_size=3, stride=1, padding=1)
        self.conv5 = torch.nn.Conv2d(64, 3, kernel_size=3, stride=1, padding=1)
        self.relu = torch.nn.ReLU(inplace=True)

    def forward(self, x):
        x = self.upsample(x)
        x = self.conv1(x)
        x = self.conv2(x)
        x = self.conv3(x)
        x = self.conv4(x)
        x = self.conv5(x)
        x = self.relu(x)
        return x

# Load your model with weights
model = StudentModel()  # Make sure to define your actual model class
model.load_state_dict(torch.load('/content/drive/MyDrive/Projects/ULX3s-Superresolution-CNN/Efficient-Teacher-Student-Distillative-Super-Resolution-Model/ESRGAN/models/SupervisedLossOnFeatureMaps_v2.pth'))  # Load the trained model weights

def format_fixed_point_value(value, num_bits):
    if value < 0:
        return f"-{num_bits}'sd{-value}"
    else:
        return f"{num_bits}'sd{value}"

def extract_and_format_weights(model):
    frac_bits = 16  # Number of fractional bits for fixed-point representation
    scale_factor = 2 ** frac_bits  # Scaling factor based on the fractional bits

    # Collect all convolution weights
    conv_weights = []
    conv_layer_indices = []

    for name, param in model.named_parameters():
        if 'conv' in name and 'weight' in name:
            weights = param.data.cpu().numpy()
            weights_scaled = np.round(weights * scale_factor).astype(np.int32)
            conv_weights.append(weights_scaled)
            conv_layer_indices.append(name.replace('.', '_'))

    # Determine the size of the 5D register
    total_convs = len(conv_weights)
    max_kernels = max(w.shape[0] for w in conv_weights)
    max_depth = max(w.shape[1] for w in conv_weights)
    max_height = max(w.shape[2] for w in conv_weights)
    max_width = max(w.shape[3] for w in conv_weights)

    formatted_weights = f"// 5D Register to store convolution weights: [ConvLayer][Kernel][Depth][Height][Width]\n"
    formatted_weights += f"// Fixed-point format: {frac_bits} fractional bits\n"
    formatted_weights += f"reg signed [31:0] conv_weights[0:{total_convs-1}][0:{max_kernels-1}][0:{max_depth-1}][0:{max_height-1}][0:{max_width-1}];\n"

    # Add initialization blocks separately
    for conv_index, (weights_scaled, conv_name) in enumerate(zip(conv_weights, conv_layer_indices)):
        num_kernels, kernel_depth, kernel_height, kernel_width = weights_scaled.shape
        formatted_weights += f"// Initialization for {conv_name}\n"
        for k in range(num_kernels):
            for d in range(kernel_depth):
                for i in range(kernel_height):
                    for j in range(kernel_width):
                        int_value = weights_scaled[k, d, i, j]
                        num_bits = int(int_value).bit_length() + 1  # +1 for the sign bit
                        formatted_weights += f"initial conv_weights[{conv_index}][{k}][{d}][{i}][{j}] = {format_fixed_point_value(int_value, num_bits)};\n"

    return formatted_weights

def extract_and_format_biases(model):
    frac_bits = 16  # Number of fractional bits for fixed-point representation
    scale_factor = 2 ** frac_bits  # Scaling factor based on the fractional bits

    # Collect all biases
    biases = []
    bias_layer_indices = []

    for name, param in model.named_parameters():
        if 'conv' in name and 'bias' in name:
            bias = param.data.cpu().numpy()
            bias_scaled = np.round(bias * scale_factor).astype(np.int32)
            biases.append(bias_scaled)
            bias_layer_indices.append(name.replace('.', '_'))

    # Determine the size of the 2D register
    total_convs = len(biases)
    max_biases = max(b.shape[0] for b in biases)

    formatted_biases = f"// 2D Register to store convolution biases: [ConvLayer][Bias]\n"
    formatted_biases += f"// Fixed-point format: {frac_bits} fractional bits\n"
    formatted_biases += f"reg signed [31:0] conv_biases[0:{total_convs-1}][0:{max_biases-1}];\n"

    # Add initialization blocks separately
    for conv_index, (bias_scaled, bias_name) in enumerate(zip(biases, bias_layer_indices)):
        num_biases = bias_scaled.shape[0]
        formatted_biases += f"// Initialization for {bias_name}\n"
        for i in range(num_biases):
            int_value = bias_scaled[i]
            num_bits = int(int_value).bit_length() + 1  # +1 for the sign bit
            formatted_biases += f"initial conv_biases[{conv_index}][{i}] = {format_fixed_point_value(int_value, num_bits)};\n"

    return formatted_biases

# Get formatted weights and biases as Verilog arrays with optimized bit lengths
formatted_weights = extract_and_format_weights(model)# Print or save the weights and biases
print(formatted_weights)  # Or save them to a file if preferred


// 5D Register to store convolution weights: [ConvLayer][Kernel][Depth][Height][Width]
// Fixed-point format: 16 fractional bits
reg signed [31:0] conv_weights[0:4][0:63][0:63][0:2][0:2];
// Initialization for conv1_weight
initial conv_weights[0][0][0][0][0] = 15'sd8400;
initial conv_weights[0][0][0][0][1] = -15'sd12340;
initial conv_weights[0][0][0][0][2] = 13'sd3527;
initial conv_weights[0][0][0][1][0] = -15'sd12066;
initial conv_weights[0][0][0][1][1] = -15'sd11606;
initial conv_weights[0][0][0][1][2] = -13'sd2983;
initial conv_weights[0][0][0][2][0] = 14'sd5793;
initial conv_weights[0][0][0][2][1] = 14'sd4791;
initial conv_weights[0][0][0][2][2] = 14'sd6601;
initial conv_weights[0][0][1][0][0] = -14'sd4491;
initial conv_weights[0][0][1][0][1] = 12'sd1269;
initial conv_weights[0][0][1][0][2] = 13'sd3175;
initial conv_weights[0][0][1][1][0] = 14'sd4569;
initial conv_weights[0][0][1][1][1] = -15'sd9277;
initial conv_weights[0][0][1][1][2] = -12'sd1853;
initial conv_weights[0][0][1][2]

In [9]:
biases = extract_and_format_biases(model)

print(biases)

// 2D Register to store convolution biases: [ConvLayer][Bias]
// Fixed-point format: 16 fractional bits
reg signed [31:0] conv_biases[0:4][0:63];
// Initialization for conv1_bias
initial conv_biases[0][0] = 14'sd7150;
initial conv_biases[0][1] = 14'sd7533;
initial conv_biases[0][2] = 15'sd11206;
initial conv_biases[0][3] = -15'sd11033;
initial conv_biases[0][4] = -14'sd6885;
initial conv_biases[0][5] = 12'sd2030;
initial conv_biases[0][6] = -13'sd3330;
initial conv_biases[0][7] = -15'sd8258;
initial conv_biases[0][8] = 14'sd7971;
initial conv_biases[0][9] = -15'sd9152;
initial conv_biases[0][10] = 12'sd1472;
initial conv_biases[0][11] = 15'sd10162;
initial conv_biases[0][12] = -13'sd2538;
initial conv_biases[0][13] = -15'sd9351;
initial conv_biases[0][14] = -14'sd4750;
initial conv_biases[0][15] = 13'sd3784;
initial conv_biases[0][16] = -14'sd7951;
initial conv_biases[0][17] = -15'sd11688;
initial conv_biases[0][18] = -15'sd11214;
initial conv_biases[0][19] = -14'sd4997;
initial conv_b